In [4]:
import pandas as pd
import plotly.express as px

weather = pd.read_csv('data/Weather_Data_reordered_all.csv', parse_dates=['Timestamp'])
solar = pd.read_csv('data/Solar_Energy_Generation.csv', parse_dates=['Timestamp'])
sites = pd.read_csv('data/Solar_Site_Details.csv')

In [12]:
# ## 2. Предобработка данных
# Объединение таблиц
df = (
    weather.merge(solar, on=['CampusKey', 'Timestamp'])
          .merge(sites, on=['CampusKey', 'SiteKey'])
          .dropna()
)

# Инжиниринг признаков
df['hour'] = df['Timestamp'].dt.hour
df['month'] = df['Timestamp'].dt.month
df['gen_ma_3h'] = df.groupby('SiteKey')['SolarGeneration'].transform(lambda x: x.rolling(3).mean())

# Сохранение обработанных данных
df.to_csv('processed_solar_data.csv', index=False)

In [13]:
# 3. Анализ временных рядов
# Суточная динамика
fig = px.line(
    df.groupby('hour')['SolarGeneration'].mean().reset_index(),
    x='hour', y='SolarGeneration',
    title='Среднесуточная генерация энергии'
)
fig.show()

In [15]:
# Сезонность
px.box(df, x='month', y='SolarGeneration',
       title='Распределение генерации по месяцам')

In [16]:
# ## 4. Зависимость от погодных условий
px.scatter_3d(
    df.sample(1000),
    x='AirTemperature',
    y='RelativeHumidity',
    z='SolarGeneration',
    color='hour',
    title='Генерация vs Температура/Влажность'
)

In [17]:
# Тепловая карта корреляций
corr_matrix = df[['SolarGeneration','AirTemperature','WindSpeed','kWp']].corr()
px.imshow(corr_matrix, text_auto=True, aspect='auto')

In [18]:
# 5. Выявление аномалий
# Метод межквартильного размаха
Q1 = df['SolarGeneration'].quantile(0.25)
Q3 = df['SolarGeneration'].quantile(0.75)
IQR = Q3 - Q1

anomalies = df[(df['SolarGeneration'] < (Q1 - 1.5*IQR)) |
               (df['SolarGeneration'] > (Q3 + 1.5*IQR))]

px.scatter(
    anomalies,
    x='Timestamp',
    y='SolarGeneration',
    color='CampusKey',
    title='Обнаруженные аномалии'
)